In [1]:
print('Hi, Jupiter!')

Hi, Jupiter!


In [7]:
!pip3 install pymystem3==0.1.10
!pip3 install pymorphy2[fast]
!pip3 install razdel
!pip3 install gensim
!pip3 install nltk
!pip3 install rusenttokenize
!pip3 install regex

  Using cached https://files.pythonhosted.org/packages/51/56/57e550b53587719e92330a79c7c0f555402d953b00700efae6d5ca53cdef/pymystem3-0.1.10-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/45/1e/0c169c6a5381e241ba7404532c16a21d86ab872c9bed8bdcd4c423954103/requests-2.24.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/a2/38/928ddce2273eaa564f6f50de919327bf3a00f091b5baba8dfa9460f3a8a8/idna-2.10-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/5e/c4/6c4fe722df5343c33226f0b4e0bb042e4dc13483228b4718baf286f86d87/certifi-2020.6.20-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/56/aa/4ef5aa67a9a62505db124a5cb5262332d1d4153462eb8fd89c9fa41e5d92/urllib3-1.25.11-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/bc/a9/01ffebfb562e4274b6487b4bb1ddec7ca55ec7510b22e4c51f14098443b8/chardet-3.0.4-py2.py3-none-any.whl
    100% |████████████████████████████████| 61kB 501kB/

  Using cached https://files.pythonhosted.org/packages/87/9f/aad666560082cb11331167cbb31cf0e8bd90af8ea4951436d1fcb2ddde44/regex-2020.10.28-cp36-cp36m-manylinux1_x86_64.whl


In [21]:
text = open('Рабочий стол/zhivago.txt','r').read()
print(text)

<author><first-name>Борис</first-name><middle-name>Леонидович</middle-name><last-name>Пастернак</last-name></author>
<book-title>Доктор Живаго</book-title>
<annotation><p>«Доктор Живаго» - итоговое произведение Бориса Пастернака, книга всей его жизни. Этот роман принес его автору мировую известность и Нобелевскую премию, присуждение которой обернулось для поэта оголтелой политической травлей, обвинениями в «измене Родине» и в результате стоило ему жизни.</p>
<p>«Доктор Живаго» - роман, сама ткань которого убедительнее свидетельствует о чуде, чем все размышления доктора и обобщения автора. Человек, который так пишет, бесконечно много пережил и передумал, и главные его чувства на свете  - восхищенное умиление и слезное сострадание; конечно, есть в его мире место и презрению, и холодному отстранению  - но не в них суть. Роман Пастернака  - оплакивание прежних заблуждений и их жертв; те, кто не разделяет молитвенного восторга перед миром, достойны прежде всего жалости. Перечитывать «Доктор

In [18]:
import string
from gensim.utils import tokenize
from gensim.summarization.textcleaner import split_sentences
from rusenttokenize import ru_sent_tokenize
from razdel import sentenize
from razdel import tokenize as razdel_tokenize
from nltk import sent_tokenize
from nltk.tokenize import word_tokenize, wordpunct_tokenize
from pymorphy2 import MorphAnalyzer
from pymystem3 import Mystem
from nltk.corpus import stopwords
from string import punctuation
import re, os, json


In [118]:
# героически пытаюсь пользоваться регулярками
# первый этап очистки, убираю теги
clean_text_tags = re.sub(r'<[^>]+>', ' ', text)
# убираю пробелы
clean_text_space = re.sub('  +', ' ', clean_text_tags)
# убираю английский слова
clean_text_eng = re.sub(r'[A-za-z].+', ' ', clean_text_space)
print(clean_text_eng)
# убираю ненужные цифры в конце и в начале после англ слов, я читер года
# простите!
clean_text_nums = re.sub(r'\n(([+]?\d+)|/|(/+?|\+|\+?\d.*))|(17.04.2008)|(\/9)|(\+)|(\/)', ' ', clean_text_eng)
#print(clean_text_nums)
# опять убираю пробелы
clean_text_spaces = re.sub('  +', ' ', clean_text_nums)
#print(clean_text_spaces)

 Борис Леонидович Пастернак 
 Доктор Живаго 
 «Доктор Живаго» - итоговое произведение Бориса Пастернака, книга всей его жизни. Этот роман принес его автору мировую известность и Нобелевскую премию, присуждение которой обернулось для поэта оголтелой политической травлей, обвинениями в «измене Родине» и в результате стоило ему жизни. 
 «Доктор Живаго» - роман, сама ткань которого убедительнее свидетельствует о чуде, чем все размышления доктора и обобщения автора. Человек, который так пишет, бесконечно много пережил и передумал, и главные его чувства на свете - восхищенное умиление и слезное сострадание; конечно, есть в его мире место и презрению, и холодному отстранению - но не в них суть. Роман Пастернака - оплакивание прежних заблуждений и их жертв; те, кто не разделяет молитвенного восторга перед миром, достойны прежде всего жалости. Перечитывать «Доктора Живаго» стоит именно тогда, когда кажется, что жить не стоит. Тогда десять строк из этого романа могут сделать то же, что делает лю

In [191]:
# делю текст на предложения
# to_sent = ru_sent_tokenize(clean_text_spaces)# Something went wrong while tokenizing!
# я испугалась, он начал виснуть, сделала по другому
sent = re.split('(?<=[\.?!]) +(?=[А-ЯЁ])', clean_text_spaces.replace('\n', ' '))
sentences = []
for s in sent:
    s.replace('\xa0',' ')
    s = re.sub('  +', ' ', s)
    #print(s)
    # вот тут лежат предложения, если что, их всегда можно достать
    s = s.lower()
    sentences.append(s)
    #print(s)
#print(sentences[:10])
# делю исходный чистый текст на токены, убираю токены-пункт знаки
string.punctuation += '«»—…“”'
string.punctuation += '–'
# собственно, вот список токенов-слов
tokens = []
tokenized_text = razdel_tokenize(clean_text_spaces.lower())
for token in tokenized_text:
    if token.text not in string.punctuation:
        tokens.append(token.text)
        print(token.text)

борис
леонидович
пастернак
доктор
живаго
доктор
живаго
итоговое
произведение
бориса
пастернака
книга
всей
его
жизни
этот
роман
принес
его
автору
мировую
известность
и
нобелевскую
премию
присуждение
которой
обернулось
для
поэта
оголтелой
политической
травлей
обвинениями
в
измене
родине
и
в
результате
стоило
ему
жизни
доктор
живаго
роман
сама
ткань
которого
убедительнее
свидетельствует
о
чуде
чем
все
размышления
доктора
и
обобщения
автора
человек
который
так
пишет
бесконечно
много
пережил
и
передумал
и
главные
его
чувства
на
свете
восхищенное
умиление
и
слезное
сострадание
конечно
есть
в
его
мире
место
и
презрению
и
холодному
отстранению
но
не
в
них
суть
роман
пастернака
оплакивание
прежних
заблуждений
и
их
жертв
те
кто
не
разделяет
молитвенного
восторга
перед
миром
достойны
прежде
всего
жалости
перечитывать
доктора
живаго
стоит
именно
тогда
когда
кажется
что
жить
не
стоит
тогда
десять
строк
из
этого
романа
могут
сделать
то
же
что
делает
любовь
в
одном
из
стихотворений
доктора
жизнь
верн

явление
разделяющее
с
прочими
государственными
установлениями
их
незыблемость
и
непогрешимость
но
настоящему
искусству
в
моем
понимании
далеко
до
таких
притязаний
где
ему
повелевать
и
предписывать
когда
слабостей
и
грехов
на
нем
больше
чем
добродетелей
оно
робко
желает
быть
мечтою
читателя
предметом
читательской
жажды
и
нуждается
в
его
отзывчивом
воображении
не
как
в
дружелюбной
снисходительности
а
как
в
составном
элементе
без
которого
не
может
обойтись
построение
художника
как
нуждается
луч
в
отражающей
поверхности
или
в
преломляющей
среде
чтобы
играть
и
загораться
надежды
автора
оправдались
картинами
полувекового
обихода
называл
пастернак
свой
роман
о
докторе
живаго
по
прошествии
второй
половины
века
и
на
рубеже
нового
он
продолжает
волновать
читателей
и
находить
живой
отклик
в
их
душах
евгений
пастернак
первая
книга
часть
первая
пятичасовой
скорый
1
шли
и
шли
и
пели
вечную
память
и
когда
останавливались
казалось
что
ее
по-залаженному
продолжают
петь
ноги
лошади
дуновения
ветра
прохо

диктовал
николай
николаевич
надо
вставить
за
отчетный
год
говорил
иван
иванович
и
записывал
террасу
слегка
проскваживало
на
листах
брошюры
лежали
куски
гранита
чтобы
они
не
разлетелись
когда
они
кончили
николай
николаевич
заторопился
домой
гроза
надвигается
надо
собираться
и
не
думайте
не
пущу
сейчас
будем
чай
пить
мне
к
вечеру
надо
обязательно
в
город
ничего
не
поможет
слышать
не
хочу
из
палисадника
тянуло
самоварной
гарью
заглушавшей
запах
табака
и
гелиотропа
туда
проносили
из
флигеля
каймак
ягоды
и
ватрушки
вдруг
пришло
сведенье
что
павел
отправился
купаться
и
повел
купать
на
реку
лошадей
николаю
николаевичу
пришлось
покориться
пойдемте
на
обрыв
посидим
на
лавочке
пока
накроют
к
чаю
предложил
иван
иванович
иван
иванович
на
правах
приятельства
занимал
у
богача
кологривова
две
комнаты
во
флигеле
управляющего
этот
домик
с
примыкающим
к
нему
палисадником
находился
в
черной
запущенной
части
парка
со
старой
полукруглою
аллеей
въезда
аллея
густо
заросла
травою
по
ней
теперь
не
было
движени

с
жирною
косметикой
когда
они
проходили
мимо
гордоновского
купе
кутая
углы
плеч
в
накидки
и
превращая
тесноту
коридора
в
источник
нового
кокетства
мише
казалось
что
они
шипят
или
судя
по
их
поджатым
губам
должны
шипеть
ах
скажите
пожалуйста
какая
чувствительность
мы
особенные
мы
интеллигенты
мы
не
можем
тело
самоубийцы
лежало
на
траве
около
насыпи
струйка
запекшейся
крови
резким
знаком
чернела
поперек
лба
и
глаз
разбившегося
перечеркивая
это
лицо
словно
крестом
вымарки
кровь
казалась
не
его
кровью
вытекшею
из
него
а
приставшим
посторонним
придатком
пластырем
или
брызгом
присохшей
грязи
или
мокрым
березовым
листком
кучка
любопытных
и
сочувствующих
вокруг
тела
все
время
менялась
над
ним
хмуро
без
выражения
стоял
его
приятель
и
сосед
по
купе
плотный
и
высокомерный
адвокат
породистое
животное
в
вымокшей
от
пота
рубашке
он
изнывал
от
жары
и
обмахивался
мягкой
шляпой
на
все
расспросы
он
нелюбезно
цедил
пожимая
плечами
и
даже
не
оборачиваясь
алкоголик
неужели
непонятно
самое
типическое
следст

целые
улицы
отданные
разврату
трущобы
погибших
созданий
детей
не
удивляла
грязь
в
номерах
клопы
убожество
меблировки
после
смерти
отца
мать
жила
в
вечном
страхе
обнищания
родя
и
лара
привыкли
слышать
что
они
на
краю
гибели
они
понимали
что
они
не
дети
улицы
но
в
них
глубоко
сидела
робость
перед
богатыми
как
у
питомцев
сиротских
домов
живой
пример
этого
страха
подавала
им
мать
амалия
карловна
была
полная
блондинка
лет
тридцати
пяти
у
которой
сердечные
припадки
сменялись
припадками
глупости
она
была
страшная
трусиха
и
смертельно
боялась
мужчин
именно
поэтому
она
с
перепугу
и
от
растерянности
все
время
попадала
к
ним
из
объятия
в
объятие
в
черногории
они
занимали
двадцать
третий
номер
а
в
двадцать
четвертом
со
дня
основания
номеров
жил
виолончелист
тышкевич
потливый
и
лысый
добряк
в
паричке
который
молитвенно
складывал
руки
и
прижимал
их
к
груди
когда
убеждал
кого-нибудь
и
закидывал
голову
назад
и
вдохновенно
закатывал
глаза
играя
в
обществе
и
выступая
на
концертах
он
редко
бывал
дома
и
н

...

кругом
я
где-нибудь
за
кустиком
никто
не
увидит
а
ты
спи
не
разговаривай
сон
разгуляешь
я
и
так
больше
не
усну
я
с
тобою
пойду
и
они
пошли
на
речку
мимо
белых
уже
успевших
накалиться
на
жарком
только
что
взошедшем
солнце
каменных
развалин
посреди
бывших
улиц
на
земле
на
самом
солнцепеке
спали
потные
храпящие
раскрасневшиеся
люди
это
были
в
большинстве
местные
оставшиеся
без
крова
старики
женщины
и
дети
редко
отбившиеся
и
нагоняющие
свои
подразделения
одиночки
красноармейцы
гордон
и
дудоров
осторожно
все
время
глядя
под
ноги
чтобы
не
наступить
на
них
ступали
между
спящими
говори
потише
а
то
разбудим
город
и
тогда
прощай
моя
стирка
и
они
вполголоса
продолжали
свой
ночной
разговор
2
что
это
за
река
не
знаю
не
спрашивал
вероятно
зуша
нет
не
зуша
какая-то
другая
ну
тогда
не
знаю
на
зуше-то
ведь
это
все
и
случилось
с
христиной
да
но
в
другом
месте
течения
где-то
ниже
говорят
церковь
ее
к
лику
святых
причла
там
было
каменное
сооружение
получившее
имя
конюшни
действительно
совхозная
конюшня
ко

сотрясением
земли
под
ногами
распрямляли
согнутые
спины
опирались
на
ручки
заступов
и
повернувши
голову
в
направлении
разразившегося
взрыва
отдыхали
долго
глядя
в
ту
сторону
там
сперва
столбами
и
фонтанами
а
потом
ленивыми
отяжелевшими
наплывами
восходили
к
небу
серые
черные
кирпично-красные
и
дымно-огненные
облака
поднятого
на
воздух
мусора
расплывались
раскидывались
султанами
рассеивались
оседали
назад
на
землю
и
работавшие
снова
брались
за
работу
одну
из
полян
на
незастроенной
стороне
окаймляли
кусты
и
покрывали
сплошной
тенью
росшие
на
ней
старые
деревья
этой
растительностью
поляна
отгораживалась
от
остального
мира
как
стоящий
особняком
и
погруженный
в
прохладный
сумрак
крытый
двор
на
поляне
бельевщица
таня
с
двумя
или
тремя
однополчанами
и
несколькими
напросившимися
попутчиками
а
также
гордон
и
дудоров
дожидались
с
утра
грузовика
высланного
за
танею
и
порученным
ей
полковым
имуществом
оно
размещено
было
в
нескольких
стоявших
на
поляне
и
горой
наставленных
ящиках
татьяна
стерегла
и

мне
ну
что
мне
теперь
делать
думаю
что
мне
делать
со
старухой
полоумною
и
разбойником
этим
душегубом
а
время-то
идет
только
я
это
подумала
слышь
под
окном
удалой
заржал
нераспряженный
ведь
он
все
время
стоял
да
заржал
удалой
словно
хочет
сказать
давай
танюша
скорей
к
добрым
людям
поскачем
помощь
позовем
а
я
гляжу
дело
к
рассвету
будь
по-твоему
думаю
спасибо
удалой
надоумил
твоя
правда
давай
слетаем
и
только
я
это
подумала
чу
слышу
словно
мне
опять
кто
из
лесу
погоди
не
торопись
танюша
мы
это
дело
по-другому
обернем
и
опять
я
в
лесу
не
одна
словно
бы
петух
по-родному
пропел
знакомый
паровоз
снизу
меня
свистком
аукнул
я
этот
паровоз
по
свистку
знала
он
в
нагорной
всегда
под
парами
стоял
толкачом
назывался
товарные
на
подъеме
подпихивать
а
это
смешанный
шел
каждую
ночь
он
в
это
время
мимо
проходил
слышу
я
стало
быть
снизу
меня
знакомый
паровоз
зовет
слышу
а
у
самой
сердце
прыгает
нужли
думаю
и
я
вместе
с
тетей
марфушей
не
в
своем
уме
что
со
мной
всякая
живая
тварь
всякая
машина
бессловесн

лес
забрасывает
как
насмешник
этот
шум
на
обрывистый
склон
где
сгоревший
на
солнце
орешник
словно
жаром
костра
опален
здесь
дорога
спускается
в
балку
здесь
и
высохших
старых
коряг
и
лоскутницы-осени
жалко
все
сметающей
в
этот
овраг
и
того
что
вселенная
проще
чем
иной
полагает
хитрец
что
как
в
воду
опущена
роща
что
приходит
всему
свой
конец
что
глазами
бессмысленно
хлопать
когда
все
пред
тобой
сожжено
и
осенняя
белая
копоть
паутиною
тянет
в
окно
ход
из
сада
в
заборе
проломан
и
теряется
в
березняке
в
доме
смех
и
хозяйственный
гомон
тот
же
гомон
и
смех
вдалеке
11
свадьба
пересекши
край
двора
гости
на
гулянку
в
дом
невесты
до
утра
перешли
с
тальянкой
за
хозяйскими
дверьми
в
войлочной
обивке
стихли
с
часу
до
семи
болтовни
обрывки
только
спать
и
спать
бы
вновь
запел
аккордеон
уходя
со
свадьбы
и
рассыпал
гармонист
снова
на
баяне
плеск
ладоней
блеск
монист
шум
и
гам
гулянья
и
опять
опять
опять
говорок
частушки
прямо
к
спящим
на
кровать
ворвался
с
пирушки
в
шуме
свисте
гаме
снова
павой
поплыла


пьют
чай
торопятся
к
трамваям
в
теченье
нескольких
минут
вид
города
неузнаваем
в
воротах
вьюга
вяжет
сеть
из
густо
падающих
хлопьев
и
чтобы
вовремя
поспеть
все
мчатся
недоев-недопив
я
чувствую
за
них
за
всех
как
будто
побывал
в
их
шкуре
я
таю
сам
как
тает
снег
я
сам
как
утро
брови
хмурю
со
мною
люди
без
имен
деревья
дети
домоседы
я
ими
всеми
побежден
и
только
в
том
моя
победа
20
чудо
он
шел
из
вифании
в
ерусалим
заранее
грустью
предчувствий
томим
колючий
кустарник
на
круче
был
выжжен
над
хижиной
ближней
не
двигался
дым
был
воздух
горяч
и
камыш
неподвижен
и
мертвого
моря
покой
недвижим
и
в
горечи
спорившей
с
горечью
моря
он
шел
с
небольшою
толпой
облаков
по
пыльной
дороге
на
чье-то
подворье
шел
в
город
на
сборище
учеников
и
так
углубился
он
в
мысли
свои
что
поле
в
унынье
запахло
полынью
все
стихло
один
он
стоял
посредине
все
перемешалось
теплынь
и
пустыня
и
ящерицы
и
ключи
и
ручьи
смоковница
высилась
невдалеке
совсем
без
плодов
только
ветки
да
листья
и
он
ей
сказал
для
какой
ты
корысти


In [176]:
# давайте искать повторяющиесяся предложения
repeating_sentences = []
for sent in sentences:
    if sentences.count(sent)>1:
        repeating_sentences.append(sent)
print(repeating_sentences[:10])

['единственно живое и яркое в вас – это то, что вы жили в одно время со мной и меня знали».', 'весной в несколько дней лес преображается, подымается до облаков, в его покрытых листьями дебрях можно затеряться, спрятаться.', 'это превращение достигается движением, по стремительности превосходящим движения животных, потому что животное не растет так быстро, как растение, и которого никогда нельзя подсмотреть.', 'лес не передвигается, мы не можем его накрыть, подстеречь за переменою места.', 'мы всегда застаем его в неподвижности.', 'и в такой же неподвижности застигаем мы вечно растущую, вечно меняющуюся, неуследимую в своих превращениях жизнь общества, историю.', 'толстой не довел своей мысли до конца, когда отрицал роль зачинателей за наполеоном, правителями, полководцами.', 'он думал именно то же самое, но не договорил этого со всею ясностью.', 'потом пришла война, разруха, и долго-долго о тебе ни слуху не было, ни духу.', 'и через много-много лет твой голос вновь меня встревожил.']


In [178]:
# теперь разбираемся с токенами, нам надо найти
#самый частотный токен в тексте длиннее 6 символов
tokens_dict = {}
for token in tokens:
    if len(token)>6:
        tokens_dict.setdefault(token, 0)
        tokens_dict[token] += 1
# сортируем словарь        
dict_sort = sorted(tokens_dict.items(),key=lambda i: i[1], reverse = True)
print(dict_sort[0])
       
        

('андреевич', 289)


In [205]:
# делаем стемминг
# у нас сейчас получится частотный список, потому что я вспомнила про Counter
# из него выберем какие нить частотные слова и проверим, что как
from collections import Counter
from nltk.stem.snowball import SnowballStemmer
stems_dict = {}
# не забываем копировать из конспекта
stemmer = SnowballStemmer('russian')
stems = [(word, stemmer.stem(word)) for word in tokens]
also_stems = set(stems)
freq_list = []
for i, stem in enumerate(also_stems):
    freq_list.append(stem[1])
common = Counter(freq_list)
print(common.most_common(10))


[('пуст', 31), ('цел', 26), ('след', 25), ('прост', 25), ('сдела', 23), ('оста', 22), ('прав', 22), ('бел', 21), ('продолжа', 21), ('ход', 21)]


'for token in tokens:\n    stem = stemmer.stem(token)\n    stems.append(stem)\n    stems_dict.setdefault(stem, 0)\n    stems_dict[stem] += 1\n# сортируем словарь        \ndict_sort = sorted(stems_dict.items(),key=lambda i: i[1], reverse = True)\nprint(dict_sort)'

In [206]:
# давайте возьмем первые 3 стемма
first = []
second = []
third = []
for stem in also_stems:
    if stem[1] == 'пуст':
        first.append(stem)
print(first[:10])        
for stem in also_stems:
    if stem[1] == 'цел':
        second.append(stem)
print(second[:10])        
for stem in also_stems:
    if stem[1] == 'след':
        third.append(stem)
print(third[:10])    

# как я поняла, из того, что в итоге распечаталось, стеммер пихает, например, в тот же "пуст" что угодно,
# хотя так не надо делать; было бы правильнее, если бы он не откусывал ь от слова пусть, и, например,
# оставил уй у целуй

[('пусти', 'пуст'), ('пустыми', 'пуст'), ('пустым', 'пуст'), ('пустят', 'пуст'), ('пустующую', 'пуст'), ('пустому', 'пуст'), ('пустующее', 'пуст'), ('пусты', 'пуст'), ('пустой', 'пуст'), ('пустого', 'пуст')]
[('целая', 'цел'), ('целую', 'цел'), ('целясь', 'цел'), ('целиться', 'цел'), ('целями', 'цел'), ('целый', 'цел'), ('целы', 'цел'), ('цела', 'цел'), ('целые', 'цел'), ('целого', 'цел')]
[('следила', 'след'), ('следующими', 'след'), ('следующую', 'след'), ('следует', 'след'), ('следам', 'след'), ('следующие', 'след'), ('следами', 'след'), ('следу', 'след'), ('следую', 'след'), ('следы', 'след')]


In [211]:
# теперь посмотрим, что там по неизменным словам
without_changes = []
for stem in stems:
        if len(stem[0]) > 4:
            if stem[0] == stem[1]:
                without_changes.append(stem)
common = Counter(without_changes)
print(common.most_common(15))
# и вот мы набдюдаем слова типа может, будет,которые надо было бы укоротить, но не получилось

[(('андреевич', 'андреевич'), 289), (('доктор', 'доктор'), 226), (('перед', 'перед'), 172), (('может', 'может'), 162), (('через', 'через'), 144), (('будет', 'будет'), 141), (('сейчас', 'сейчас'), 127), (('человек', 'человек'), 112), (('вдруг', 'вдруг'), 109), (('поезд', 'поезд'), 65), (('видел', 'видел'), 53), (('назад', 'назад'), 49), (('гордон', 'гордон'), 47), (('город', 'город'), 45), (('хотел', 'хотел'), 45)]


In [222]:
# я не успела сделать 4 задание, потому что отложила его на ненаступившее потом, но частично успела 5, вот оно:
# итак, я сравниваю майстем и пайморфи
mystem = Mystem()
morph = MorphAnalyzer()
print(mystem.lemmatize(clean_text_spaces)[:100])
#  мне не понравилось, что тут к словам цепляется ',\xa0– '? если распечатывать кучу всего

[' ', 'борис', ' ', 'леонидович', ' ', 'пастернак', ' \n', ' ', 'доктор', ' ', 'живаго', ' \n', ' «', 'доктор', ' ', 'живаго', '» - ', 'итоговый', ' ', 'произведение', ' ', 'борис', ' ', 'пастернак', ', ', 'книга', ' ', 'весь', ' ', 'его', ' ', 'жизнь', '. ', 'этот', ' ', 'роман', ' ', 'приносить', ' ', 'он', ' ', 'автор', ' ', 'мировой', ' ', 'известность', ' ', 'и', ' ', 'нобелевский', ' ', 'премия', ', ', 'присуждение', ' ', 'который', ' ', 'обертываться', ' ', 'для', ' ', 'поэт', ' ', 'оголтелый', ' ', 'политический', ' ', 'травля', ', ', 'обвинение', ' ', 'в', ' «', 'измена', ' ', 'родина', '» ', 'и', ' ', 'в', ' ', 'результат', ' ', 'стоить', ' ', 'он', ' ', 'жизнь', '.', ' \n', ' «', 'доктор', ' ', 'живаго', '» - ', 'роман', ', ', 'сам', ' ', 'ткань']


In [220]:
words_analized = mystem.analyze(clean_text_spaces)
print(words_analized[:50])
# эти вещи вообще нечитаемые, я пыталась понять, как тут что то смотреть, но у меня уже болели глаза, простите, это все, что я смогла сделать
# я думаю, будет прекрасно, если вы мне объясните, как тут привести все к человекочитаемому виду и тогда я смогу доделать

[{'text': ' '}, {'analysis': [{'lex': 'борис', 'wt': 1, 'gr': 'S,имя,муж,од=им,ед'}], 'text': 'Борис'}, {'text': ' '}, {'analysis': [{'lex': 'леонидович', 'wt': 1, 'gr': 'S,отч,муж,од=им,ед'}], 'text': 'Леонидович'}, {'text': ' '}, {'analysis': [{'lex': 'пастернак', 'wt': 0.895624864, 'gr': 'S,фам,муж,од=им,ед'}], 'text': 'Пастернак'}, {'text': ' \n'}, {'text': ' '}, {'analysis': [{'lex': 'доктор', 'wt': 1, 'gr': 'S,муж,од=им,ед'}], 'text': 'Доктор'}, {'text': ' '}, {'analysis': [{'lex': 'живаго', 'wt': 1, 'gr': 'S,фам,мж,од=(пр,мн|пр,ед|вин,мн|вин,ед|дат,мн|дат,ед|род,мн|род,ед|твор,мн|твор,ед|им,мн|им,ед)'}], 'text': 'Живаго'}, {'text': ' \n'}, {'text': ' «'}, {'analysis': [{'lex': 'доктор', 'wt': 1, 'gr': 'S,муж,од=им,ед'}], 'text': 'Доктор'}, {'text': ' '}, {'analysis': [{'lex': 'живаго', 'wt': 1, 'gr': 'S,фам,мж,од=(пр,мн|пр,ед|вин,мн|вин,ед|дат,мн|дат,ед|род,мн|род,ед|твор,мн|твор,ед|им,мн|им,ед)'}], 'text': 'Живаго'}, {'text': '» - '}, {'analysis': [{'lex': 'итоговый', 'wt': 1, 

In [221]:
# основная функция - pymorphy.parse
words_analized = [morph.parse(token) for token in word_tokenize(clean_text_spaces)]
print(words_analized[:100])

[[Parse(word='борис', tag=OpencorporaTag('NOUN,anim,masc,Name sing,nomn'), normal_form='борис', score=1.0, methods_stack=((DictionaryAnalyzer(), 'борис', 27, 0),))], [Parse(word='леонидович', tag=OpencorporaTag('NOUN,anim,masc,Patr sing,nomn'), normal_form='леонидович', score=1.0, methods_stack=((DictionaryAnalyzer(), 'леонидович', 26, 0),))], [Parse(word='пастернак', tag=OpencorporaTag('NOUN,inan,masc sing,nomn'), normal_form='пастернак', score=0.3333333333333333, methods_stack=((DictionaryAnalyzer(), 'пастернак', 19, 0),)), Parse(word='пастернак', tag=OpencorporaTag('NOUN,inan,masc sing,accs'), normal_form='пастернак', score=0.3333333333333333, methods_stack=((DictionaryAnalyzer(), 'пастернак', 19, 3),)), Parse(word='пастернак', tag=OpencorporaTag('NOUN,anim,masc,Sgtm,Surn sing,nomn'), normal_form='пастернак', score=0.3333333333333333, methods_stack=((DictionaryAnalyzer(), 'пастернак', 3254, 0),))], [Parse(word='доктор', tag=OpencorporaTag('NOUN,anim,masc sing,nomn'), normal_form='до